In [9]:
import pandas as pd
pd.set_option('future.no_silent_downcasting', True)

In [10]:
import numpy as np
from sklearn.model_selection import KFold

In [11]:
from skrub import TableVectorizer
import time 

In [12]:
from benchy.kaggle import METADATA, fetch_playground_series
from lightgbm import LGBMClassifier
from catboost import CatBoostClassifier
from xgboost import XGBClassifier
from sklearn.pipeline import make_pipeline
from sklearn.linear_model import LogisticRegression
from skrub import TableVectorizer
from sklearn.ensemble import HistGradientBoostingClassifier, RandomForestClassifier, GradientBoostingClassifier
from sklearn.metrics import classification_report, mean_absolute_error, mean_squared_error, r2_score 
from sklearn.preprocessing import LabelEncoder

def calc_scores(task, y_true, y_pred):
    if task == "classification":
        return classification_report(y_true, y_pred, output_dict=True)
    if task == "regression":
        return {
            "mae": mean_absolute_error(y_true, y_pred),
            "mse": mean_squared_error(y_true, y_pred),
            "r2": r2_score(y_true, y_pred)
        }

def get_datasets(task="classification"):
    for name, descr in METADATA.items():
        if descr['task'] == task:
            season = int(name.split("e")[0].replace("s", ""))
            episode = int(name.split("e")[1])
            yield name, fetch_playground_series(season, episode, return_X_y=True)

def get_featurizers(task="classification", elaborate=False):
    yield "tablevec", TableVectorizer()
    
def get_estimators(task="classification", elaborate=False):
    if task == "classification":
        yield "lr", LogisticRegression()
        yield "hgbt", HistGradientBoostingClassifier()
        yield "rf", RandomForestClassifier()
        yield "gbt", GradientBoostingClassifier()
        yield "xgboost", XGBClassifier()
        yield "catboost", CatBoostClassifier()
        yield "lgbm", LGBMClassifier()

In [13]:
def task_generator(task, n_seeds=1, n_splits=5, dry_run=False):
    for dataname, (X, y) in get_datasets(task):
        for random_seed in range(n_seeds):
            kf = KFold(n_splits=n_splits, shuffle=True, random_state=random_seed)
            for cv_id, (train_idx, test_idx) in enumerate(kf.split(X)):
                for tfm_name, tfm in get_featurizers(task, elaborate=False):
                    for mod_name, mod in get_estimators(task, elaborate=False):
                        if dry_run:
                            yield 1
                        else:
                            X_train, X_test = X[train_idx], X[test_idx]
                            y_train, y_test = y[train_idx], y[test_idx]
                            yield {
                                "task": task,
                                "dataname": dataname,
                                "random_seed": random_seed,
                                "cv_id": cv_id,
                                "tfm_name": tfm_name,
                                "mod_name": mod_name,
                                "featurizer": tfm,
                                "model": mod,
                                "datasets": (X_train, X_test, y_train, y_test)
                            }

def train(task, dataname, random_seed, cv_id, tfm_name, mod_name, featurizer, model, datasets):
    X_train, X_test, y_train, y_test = datasets
    
    # XGBoost doesnt handle this nicely internally, so we gotta do this manually
    lab_enc = LabelEncoder()
    y_train = lab_enc.fit_transform(y_train)
    y_test = lab_enc.transform(y_test)
    
    # Sometimes featurization can take embarassingly long, inspect.
    tic = time.time()
    featurizer.fit(X_train, y_train)
    feat_time = time.time() - tic

    # Train the model
    tic = time.time()
    X_feat = featurizer.transform(X_train)
    model.fit(X_feat, y_train)
    train_time = time.time() - tic

    # Keep predictions around for reporting.
    pred_train = model.predict(X_feat)

    print(y_train, pred_train)
    # Gather predictions for test set
    tic = time.time()
    X_feat_test = featurizer.transform(X_test)
    pred_test = model.predict(X_feat_test)
    infer_time = time.time() - tic

    return {
        "timestamp": int(time.time()),
        "dataname": dataname,
        "cv_id": cv_id,
        "random_seed": random_seed,
        "estimator_name": f"{mod_name}-{tfm_name}",
        "feat_time": feat_time,
        "train_time": train_time,
        "infer_time": infer_time,
        "scores_train": calc_scores(task, y_train, pred_train),
        "scores_test": calc_scores(task, y_test, pred_test)
    }

In [17]:
sum(task_generator(task="classification", dry_run=True))

420

In [18]:
from math import sqrt
import srsly 
from joblib import Parallel, delayed

parallel = Parallel(n_jobs=2, return_as="generator")

output_generator = parallel(delayed(train)(**kwargs) for kwargs in task_generator(task="classification"))

In [19]:
for item in output_generator:
    srsly.write_jsonl("output-elaborate.jsonl", [item], append=True, append_new_line=False)

/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  column = column.replace(STR_NA_VALUES, np.nan).replace(r"^\s+$", np.nan, regex=True)
/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  column = column.replace(STR_NA_VALUES, np.nan).replace(r"^\s+$", np.nan, regex=True)
/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning

[2 0 2 ... 0 2 2] [2 0 0 ... 0 0 0]
[2 0 2 ... 0 2 2] [2 0 2 ... 0 2 2]
[2 0 2 ... 0 2 2] [2 0 2 ... 0 2 2]
Learning rate set to 0.086931
0:	learn: 1.0088458	total: 66.5ms	remaining: 1m 6s
1:	learn: 0.9393293	total: 82ms	remaining: 40.9s
2:	learn: 0.8817560	total: 93.9ms	remaining: 31.2s
3:	learn: 0.8325919	total: 106ms	remaining: 26.3s
4:	learn: 0.7920052	total: 122ms	remaining: 24.3s
5:	learn: 0.7555721	total: 138ms	remaining: 22.9s
6:	learn: 0.7236734	total: 150ms	remaining: 21.3s
7:	learn: 0.6952497	total: 163ms	remaining: 20.3s
8:	learn: 0.6710740	total: 177ms	remaining: 19.5s
9:	learn: 0.6494727	total: 189ms	remaining: 18.7s
10:	learn: 0.6308615	total: 200ms	remaining: 18s
11:	learn: 0.6138240	total: 208ms	remaining: 17.1s
12:	learn: 0.5988273	total: 214ms	remaining: 16.2s
13:	learn: 0.5851263	total: 221ms	remaining: 15.6s
14:	learn: 0.5743742	total: 228ms	remaining: 15s
15:	learn: 0.5633631	total: 235ms	remaining: 14.5s
16:	learn: 0.5539018	total: 243ms	remaining: 14.1s
17:	lear

/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  column = column.replace(STR_NA_VALUES, np.nan).replace(r"^\s+$", np.nan, regex=True)
/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  column = column.replace(STR_NA_VALUES, np.nan).replace(r"^\s+$", np.nan, regex=True)
/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning

157:	learn: 0.3685803	total: 1.79s	remaining: 9.57s
158:	learn: 0.3680439	total: 1.81s	remaining: 9.58s
159:	learn: 0.3675154	total: 1.82s	remaining: 9.58s
160:	learn: 0.3667699	total: 1.84s	remaining: 9.59s
161:	learn: 0.3664774	total: 1.85s	remaining: 9.59s
162:	learn: 0.3660124	total: 1.87s	remaining: 9.58s
163:	learn: 0.3654985	total: 1.88s	remaining: 9.59s
164:	learn: 0.3650151	total: 1.89s	remaining: 9.58s
165:	learn: 0.3643115	total: 1.91s	remaining: 9.58s
166:	learn: 0.3637881	total: 1.92s	remaining: 9.58s
167:	learn: 0.3635521	total: 1.94s	remaining: 9.59s
168:	learn: 0.3631072	total: 1.95s	remaining: 9.58s
169:	learn: 0.3624824	total: 1.96s	remaining: 9.58s
170:	learn: 0.3619477	total: 1.98s	remaining: 9.58s
171:	learn: 0.3613563	total: 1.99s	remaining: 9.58s
172:	learn: 0.3608713	total: 2s	remaining: 9.58s
173:	learn: 0.3605098	total: 2.02s	remaining: 9.58s
174:	learn: 0.3598266	total: 2.03s	remaining: 9.57s
175:	learn: 0.3594930	total: 2.04s	remaining: 9.57s
176:	learn: 0.3

/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  column = column.replace(STR_NA_VALUES, np.nan).replace(r"^\s+$", np.nan, regex=True)
/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  column = column.replace(STR_NA_VALUES, np.nan).replace(r"^\s+$", np.nan, regex=True)
/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning

...

/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  column = column.replace(STR_NA_VALUES, np.nan).replace(r"^\s+$", np.nan, regex=True)
/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  column = column.replace(STR_NA_VALUES, np.nan).replace(r"^\s+$", np.nan, regex=True)
/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning

:	learn: 0.0746332	total: 3.29s	remaining: 116ms
966:	learn: 0.0744739	total: 3.29s	remaining: 112ms
967:	learn: 0.0744140	total: 3.29s	remaining: 109ms
968:	learn: 0.0742941	total: 3.3s	remaining: 106ms
969:	learn: 0.0741425	total: 3.3s	remaining: 102ms
970:	learn: 0.0739580	total: 3.3s	remaining: 98.6ms
971:	learn: 0.0738564	total: 3.3s	remaining: 95.2ms
972:	learn: 0.0737218	total: 3.31s	remaining: 91.7ms
973:	learn: 0.0736386	total: 3.31s	remaining: 88.3ms
974:	learn: 0.0735290	total: 3.31s	remaining: 84.9ms
975:	learn: 0.0733521	total: 3.31s	remaining: 81.5ms
976:	learn: 0.0732554	total: 3.31s	remaining: 78ms
977:	learn: 0.0731743	total: 3.31s	remaining: 74.6ms
978:	learn: 0.0731028	total: 3.32s	remaining: 71.2ms
979:	learn: 0.0729376	total: 3.32s	remaining: 67.8ms
980:	learn: 0.0729029	total: 3.32s	remaining: 64.3ms
981:	learn: 0.0728574	total: 3.32s	remaining: 60.9ms
982:	learn: 0.0727746	total: 3.33s	remaining: 57.5ms
983:	learn: 0.0726292	total: 3.33s	remaining: 54.1ms
984:	le

/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  column = column.replace(STR_NA_VALUES, np.nan).replace(r"^\s+$", np.nan, regex=True)
/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  column = column.replace(STR_NA_VALUES, np.nan).replace(r"^\s+$", np.nan, regex=True)
/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning

85s	remaining: 908ms
883:	learn: 0.0749874	total: 6.86s	remaining: 901ms
884:	learn: 0.0749539	total: 6.87s	remaining: 893ms
885:	learn: 0.0748913	total: 6.88s	remaining: 885ms
886:	learn: 0.0748744	total: 6.89s	remaining: 878ms
887:	learn: 0.0748607	total: 6.9s	remaining: 870ms
888:	learn: 0.0748422	total: 6.91s	remaining: 862ms
889:	learn: 0.0747994	total: 6.91s	remaining: 854ms
890:	learn: 0.0747848	total: 6.92s	remaining: 847ms
891:	learn: 0.0747637	total: 6.93s	remaining: 839ms
892:	learn: 0.0747199	total: 6.94s	remaining: 831ms
893:	learn: 0.0746713	total: 6.95s	remaining: 824ms
894:	learn: 0.0746401	total: 6.96s	remaining: 817ms
895:	learn: 0.0746140	total: 6.97s	remaining: 810ms
896:	learn: 0.0745810	total: 6.99s	remaining: 802ms
897:	learn: 0.0745323	total: 7s	remaining: 795ms
898:	learn: 0.0744826	total: 7.01s	remaining: 787ms
899:	learn: 0.0744228	total: 7.01s	remaining: 779ms
900:	learn: 0.0743879	total: 7.02s	remaining: 772ms
901:	learn: 0.0743674	total: 7.03s	remaining: 7

/usr/local/python/3.10.13/lib/python3.10/site-packages/skrub/_table_vectorizer.py:101: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  column = column.replace(STR_NA_VALUES, np.nan).replace(r"^\s+$", np.nan, regex=True)


In [15]:
import polars as pl 

In [16]:
pl.read_ndjson("output.jsonl").head(1)

FileNotFoundError: No such file or directory (os error 2): output.jsonl

In [17]:
pl.col("scores_train").struct.field("a")

<Expr ['col("scores_train").struct.fie…'] at 0x7C5E9AA2AC50>

In [59]:
df_summary = (
    pl.read_ndjson("output-elaborate.jsonl")
        .with_columns(
            acc=pl.col("scores_test").struct.field("accuracy"),
            macro_f1=pl.col("scores_test").struct.field("macro avg").struct.field("f1-score")
        )
        .group_by("dataname", "estimator_name")
        .agg(pl.mean("train_time", "feat_time", "infer_time", "acc", "macro_f1"))
        .sort("dataname", "estimator_name")
        .with_columns(
            perf_ratio=pl.col("macro_f1") / pl.max("macro_f1").over("dataname"),
            train_ratio=pl.col("train_time") / pl.mean("train_time").over("dataname"),
            infer_ratio=pl.col("infer_time") / pl.max("infer_time").over("dataname"),
        )
)

In [31]:
import altair as alt

In [33]:
(alt.Chart(df_summary)
  .mark_line()
  .encode(x=alt.X('estimator_name', sort=["tv-lr", "tv-hgbt", "tv-rf", "tv-gbt"]), y=alt.Y('macro_f1'), color=alt.Color('dataname'))
  .properties(width=600, height=250)
  .interactive())

alt.Chart(...)

In [41]:
df_summary.pivot(index='dataname', columns='estimator_name', values='macro_f1')

shape: (12, 8)
┌──────────┬────────────┬────────────┬────────────┬────────────┬───────────┬───────────┬───────────┐
│ dataname ┆ catboost-t ┆ gbt-tablev ┆ hgbt-table ┆ lgbm-table ┆ lr-tablev ┆ rf-tablev ┆ xgboost-t │
│ ---      ┆ ablevec    ┆ ec         ┆ vec        ┆ vec        ┆ ec        ┆ ec        ┆ ablevec   │
│ str      ┆ ---        ┆ ---        ┆ ---        ┆ ---        ┆ ---       ┆ ---       ┆ ---       │
│          ┆ f64        ┆ f64        ┆ f64        ┆ f64        ┆ f64       ┆ f64       ┆ f64       │
╞══════════╪════════════╪════════════╪════════════╪════════════╪═══════════╪═══════════╪═══════════╡
│ s3e10    ┆ 0.972931   ┆ 0.972262   ┆ 0.972244   ┆ 0.971106   ┆ 0.967526  ┆ 0.972146  ┆ 0.972405  │
│ s3e12    ┆ 0.700187   ┆ 0.688839   ┆ 0.682026   ┆ 0.668736   ┆ 0.704723  ┆ 0.707644  ┆ 0.637455  │
│ s3e13    ┆ 0.285726   ┆ 0.282365   ┆ 0.287653   ┆ 0.275138   ┆ 0.259772  ┆ 0.277238  ┆ 0.285225  │
│ s3e17    ┆ 0.930636   ┆ 0.92665    ┆ 0.929871   ┆ 0.930008   ┆ 0.743458  ┆ 0.926197  ┆ 0.929547  │
│ s3e2     ┆ 0.568918   ┆ 0.538583   ┆ 0.538564   ┆ 0.563276   ┆ 0.514144  ┆ 0.539318  ┆ 0.583838  │
│ …        ┆ …          ┆ …          ┆ …          ┆ …          ┆ …         ┆ …         ┆ …         │
│ s3e24    ┆ 0.78411    ┆ 0.774372   ┆ 0.780095   ┆ 0.780439   ┆ 0.730335  ┆ 0.773548  ┆ 0.779998  │
│ s3e26    ┆ 0.612099   ┆ 0.614178   ┆ 0.637716   ┆ 0.642353   ┆ 0.489693  ┆ 0.591744  ┆ 0.638508  │
│ s3e3     ┆ 0.591495   ┆ 0.651253   ┆ 0.628172   ┆ 0.601387   ┆ 0.47253   ┆ 0.543166  ┆ 0.638993  │
│ s3e4     ┆ 0.510182   ┆ 0.517144   ┆ 0.525673   ┆ 0.50513    ┆ 0.511418  ┆ 0.502059  ┆ 0.507793  │
│ s3e7     ┆ 0.811865   ┆ 0.795641   ┆ 0.810375   ┆ 0.810647   ┆ 0.736949  ┆ 0.790307  ┆ 0.812447  │
└──────────┴────────────┴────────────┴────────────┴────────────┴───────────┴───────────┴───────────┘

In [67]:
import polars.selectors as cs
from great_tables import GT, style, loc

metric = 'train_time'

pltr = df_summary.pivot(index='dataname', columns='estimator_name', values=metric).drop('lr-tablevec')
max_vals = pltr.drop('dataname').min_horizontal()
numeric_columns = [c for c in pltr.columns if c != 'dataname' and 'lr' not in c]

tbl = (
    GT(pltr)
    .tab_header(title="Classification Results", subtitle=f'Reporting on {metric}. Lower is better.')
    .fmt_number(columns=numeric_columns, decimals=4)
)

for c in numeric_columns:
    tbl = tbl.tab_style(style.text(weight='bold'), loc.body(c, pl.col(c) == max_vals))

tbl

GT(_tbl_data=shape: (12, 7)
┌──────────┬──────────────┬──────────────┬──────────────┬──────────────┬─────────────┬─────────────┐
│ dataname ┆ catboost-tab ┆ gbt-tablevec ┆ hgbt-tableve ┆ lgbm-tableve ┆ rf-tablevec ┆ xgboost-tab │
│ ---      ┆ levec        ┆ ---          ┆ c            ┆ c            ┆ ---         ┆ levec       │
│ str      ┆ ---          ┆ f64          ┆ ---          ┆ ---          ┆ f64         ┆ ---         │
│          ┆ f64          ┆              ┆ f64          ┆ f64          ┆             ┆ f64         │
╞══════════╪══════════════╪══════════════╪══════════════╪══════════════╪═════════════╪═════════════╡
│ s3e10    ┆ 29.094152    ┆ 35.856793    ┆ 1.284515     ┆ 1.305786     ┆ 29.363907   ┆ 0.932654    │
│ s3e12    ┆ 1.997388     ┆ 0.178426     ┆ 0.141473     ┆ 0.055688     ┆ 0.220111    ┆ 0.062428    │
│ s3e13    ┆ 46.91049     ┆ 3.016865     ┆ 4.060372     ┆ 0.739478     ┆ 0.342982    ┆ 0.593125    │
│ s3e17    ┆ 59.542945    ┆ 72.065774    ┆ 9.880921     ┆ 11.409694    ┆ 47.826737   ┆ 10.736755   │
│ s3e2     ┆ 89.668777    ┆ 1.794932     ┆ 0.468049     ┆ 0.44731      ┆ 1.29099     ┆ 0.404117    │
│ …        ┆ …            ┆ …            ┆ …            ┆ …            ┆ …           ┆ …           │
│ s3e24    ┆ 44.534358    ┆ 37.82906     ┆ 4.430565     ┆ 3.415148     ┆ 39.438658   ┆ 1.884457    │
│ s3e26    ┆ 13.065075    ┆ 5.797495     ┆ 2.175976     ┆ 0.860362     ┆ 1.784983    ┆ 1.135329    │
│ s3e3     ┆ 38.188448    ┆ 0.903108     ┆ 0.807938     ┆ 11.780131    ┆ 0.513892    ┆ 11.386537   │
│ s3e4     ┆ 60.51035     ┆ 301.340709   ┆ 2.344324     ┆ 5.503182     ┆ 345.879161  ┆ 4.169692    │
│ s3e7     ┆ 14.327004    ┆ 4.84396      ┆ 1.373874     ┆ 0.619009     ┆ 5.598203    ┆ 0.448311    │
└──────────┴──────────────┴──────────────┴──────────────┴──────────────┴─────────────┴─────────────┘, _body=<great_tables._gt_data.Body object at 0x7c5e91575660>, _boxhead=Boxhead([ColInfo(var='dataname', type=<ColInfoTypeEnum.default: 1>, column_label='dataname', column_align='left', column_width=None), ColInfo(var='catboost-tablevec', type=<ColInfoTypeEnum.default: 1>, column_label='catboost-tablevec', column_align='right', column_width=None), ColInfo(var='gbt-tablevec', type=<ColInfoTypeEnum.default: 1>, column_label='gbt-tablevec', column_align='right', column_width=None), ColInfo(var='hgbt-tablevec', type=<ColInfoTypeEnum.default: 1>, column_label='hgbt-tablevec', column_align='right', column_width=None), ColInfo(var='lgbm-tablevec', type=<ColInfoTypeEnum.default: 1>, column_label='lgbm-tablevec', column_align='right', column_width=None), ColInfo(var='rf-tablevec', type=<ColInfoTypeEnum.default: 1>, column_label='rf-tablevec', column_align='right', column_width=None), ColInfo(var='xgboost-tablevec', type=<ColInfoTypeEnum.default: 1>, column_label='xgboost-tablevec', column_align='right', column_width=None)]), _stub=Stub([RowInfo(rownum_i=0, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=1, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=2, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=3, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=4, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=5, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=6, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=7, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=8, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=9, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=10, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=11, group_id=None, rowname=None, group_label=None, built=False)]), _row_groups=[], _group_rows=GroupRows([]), _spanners=Spanners([]), _heading=Heading(title='Classification Results', subtitle='Reporting

In [76]:
metric = 'macro_f1'

pltr = df_summary.pivot(index='dataname', columns='estimator_name', values=metric).drop('catboost-tablevec', 'gbt-tablevec', 'rf-tablevec')
max_vals = pltr.drop('dataname').max_horizontal()
numeric_columns = [c for c in pltr.columns if c != 'dataname']

tbl = (
    GT(pltr)
    .tab_header(title="Classification Results", subtitle=f'Reporting on {metric}. Higher is better.')
    .fmt_number(columns=numeric_columns, decimals=4)
)

for c in numeric_columns:
    tbl = tbl.tab_style(style.text(weight='bold'), loc.body(c, pl.col(c) == max_vals))

tbl

GT(_tbl_data=shape: (12, 5)
┌──────────┬───────────────┬───────────────┬─────────────┬──────────────────┐
│ dataname ┆ hgbt-tablevec ┆ lgbm-tablevec ┆ lr-tablevec ┆ xgboost-tablevec │
│ ---      ┆ ---           ┆ ---           ┆ ---         ┆ ---              │
│ str      ┆ f64           ┆ f64           ┆ f64         ┆ f64              │
╞══════════╪═══════════════╪═══════════════╪═════════════╪══════════════════╡
│ s3e10    ┆ 0.972244      ┆ 0.971106      ┆ 0.967526    ┆ 0.972405         │
│ s3e12    ┆ 0.682026      ┆ 0.668736      ┆ 0.704723    ┆ 0.637455         │
│ s3e13    ┆ 0.287653      ┆ 0.275138      ┆ 0.259772    ┆ 0.285225         │
│ s3e17    ┆ 0.929871      ┆ 0.930008      ┆ 0.743458    ┆ 0.929547         │
│ s3e2     ┆ 0.538564      ┆ 0.563276      ┆ 0.514144    ┆ 0.583838         │
│ …        ┆ …             ┆ …             ┆ …           ┆ …                │
│ s3e24    ┆ 0.780095      ┆ 0.780439      ┆ 0.730335    ┆ 0.779998         │
│ s3e26    ┆ 0.637716      ┆ 0.642353      ┆ 0.489693    ┆ 0.638508         │
│ s3e3     ┆ 0.628172      ┆ 0.601387      ┆ 0.47253     ┆ 0.638993         │
│ s3e4     ┆ 0.525673      ┆ 0.50513       ┆ 0.511418    ┆ 0.507793         │
│ s3e7     ┆ 0.810375      ┆ 0.810647      ┆ 0.736949    ┆ 0.812447         │
└──────────┴───────────────┴───────────────┴─────────────┴──────────────────┘, _body=<great_tables._gt_data.Body object at 0x7c5e9169a920>, _boxhead=Boxhead([ColInfo(var='dataname', type=<ColInfoTypeEnum.default: 1>, column_label='dataname', column_align='left', column_width=None), ColInfo(var='hgbt-tablevec', type=<ColInfoTypeEnum.default: 1>, column_label='hgbt-tablevec', column_align='right', column_width=None), ColInfo(var='lgbm-tablevec', type=<ColInfoTypeEnum.default: 1>, column_label='lgbm-tablevec', column_align='right', column_width=None), ColInfo(var='lr-tablevec', type=<ColInfoTypeEnum.default: 1>, column_label='lr-tablevec', column_align='right', column_width=None), ColInfo(var='xgboost-tablevec', type=<ColInfoTypeEnum.default: 1>, column_label='xgboost-tablevec', column_align='right', column_width=None)]), _stub=Stub([RowInfo(rownum_i=0, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=1, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=2, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=3, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=4, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=5, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=6, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=7, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=8, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=9, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=10, group_id=None, rowname=None, group_label=None, built=False), RowInfo(rownum_i=11, group_id=None, rowname=None, group_label=None, built=False)]), _row_groups=[], _group_rows=GroupRows([]), _spanners=Spanners([]), _heading=Heading(title='Classification Results', subtitle='Reporting on macro_f1. Higher is better.', preheader=None), _stubhead=None, _source_notes=[], _footnotes=[], _styles=[StyleInfo(locname='data', locnum=5, grpname=None, colname='hgbt-tablevec', rownum=2, colnum=None, styles=[CellStyleText(color=None, font=None, size=None, align=None, v_align=None, style=None, weight='bold', stretch=None, decorate=None, transform=None, whitespace=None)]), StyleInfo(locname='data', locnum=5, grpname=None, colname='hgbt-tablevec', rownum=5, colnum=None, styles=[CellStyleText(color=None, font=None, size=None, align=None, v_align=None, style=None, weight='bold', stretch=None, decorate=None, transform=None, whitespace=None)]), StyleInfo(locname='data', locnum=5, grpname=None, colname='hgbt-tablevec', rownum=10, colnum=None, styles=[CellStyleT